## Major Notes

1. Per-Slot-Cost Function is currently dummy implementation because of difficulty in implementing piece-wise cost function in Gurobi
2. There are large discprepencies and missing zipcodes between poulation_calculated.demand_classification, and childcare regulated_cleaned csv files
3. Final desert removal constraints use not-strict inequalities, which are innapropriate


In [7]:
import gurobipy as gp
from gurobipy import GRB
import numpy as np
import pandas as pd


model = gp.Model()
#model.setObjective(0, GRB.MINIMIZE)
obj = 0 #we add our expressions to this to make the final obj func, and set it with model.setObjective(obj, GRB.MINIMIZE)





### Load Data into dataframes

In [8]:
#load data and sheets
demand_class = pd.read_csv("Project 1 Data- version 0.0- Yue Chen/demand_classification.csv")
zips_cleaned = demand_class["zip_code_cleaned"]
populations = pd.read_csv("/Users/phroog/Documents/Columbia/opt_models/proj1/Project 1 Data- version 0.0- Yue Chen/population_calculated.csv")
#note, ignore children capacity and just use children capacity, as it is inconsistent ( could benefit from inspection)
regulated = pd.read_csv("/Users/phroog/Documents/Columbia/opt_models/proj1/Project 1 Data- version 0.0- Yue Chen/child_care_regulated_cleaned.csv")
#to regulated we are adding 0-5 and 5-12 columns
regulated["0-5_capacity"] = regulated["infant_capacity"] + regulated["toddler_capacity"] + regulated["preschool_capacity"]
#simple rename for 5-12, SUBJECT TO ADJUSTMENT
regulated["5-12_capacity"] = regulated["school_age_capacity"]

#HERE CHECK THAT 0-5 + 5-12 CAPCITIES ADD UP TO TOTAL_CAPACITY IN REGULATED DATAFRAME

#### Per-Slot Cost Function

In [9]:
#define the per slot expansion cost function (piecewise)

#doesnt work right now because of conditionals
# def expansion_cost(ratio,new_slots,current_cap):
#     if new_slots == 0:
#         return 0
#     if ratio > 0 and ratio <= (1/3):
#         return 500*new_slots + (20000 + 200*current_cap)
#     if ratio > 1/3 and ratio <= (2/3):
#         return 400*new_slots + (20000 + 200*current_cap)
#     if ratio > 2/3 and ratio <= (1):
#         return 300*new_slots + (20000 + 200*current_cap)
#     if ratio > 1 and ratio <= (1.2):
#         return 200*new_slots + (20000 + 200*current_cap)
#     #catch rest, and throw expception
#     raise Exception("Expansion Cost Condition Unmet")

#dummy placehold function

def expansion_cost(ratio,new_slots,current_cap):
    return 20000 + (400*new_slots)/current_cap


#### Examining missing zip codes

In [10]:
# get unique zip sets
zips_pop = set(populations['zip_code_cleaned'])
zips_reg = set(regulated['zip_code_cleaned'])

# zips in regulated but not in population
missing_in_pop = zips_reg - zips_pop

# zips in population but not in regulated
missing_in_reg = zips_pop - zips_reg

print(f"Zips in regulated but not in population: {len(missing_in_pop)}")
print(sorted(missing_in_pop))

print(f"\nZips in population but not in regulated: {len(missing_in_reg)}")
print(sorted(missing_in_reg))


Zips in regulated but not in population: 116
[10166, 11453, 11582, 12220, 12240, 12242, 12557, 13261, 14124, 14428, 14454, 14467, 14469, 14471, 14480, 14482, 14485, 14487, 14489, 14502, 14506, 14507, 14512, 14513, 14514, 14517, 14519, 14522, 14527, 14530, 14534, 14539, 14543, 14550, 14551, 14559, 14572, 14581, 14591, 14604, 14605, 14606, 14607, 14610, 14611, 14613, 14614, 14615, 14616, 14618, 14619, 14620, 14624, 14626, 14701, 14706, 14712, 14715, 14716, 14718, 14719, 14733, 14737, 14738, 14739, 14743, 14750, 14757, 14760, 14769, 14779, 14782, 14787, 14801, 14802, 14803, 14804, 14807, 14809, 14810, 14813, 14814, 14821, 14823, 14826, 14830, 14837, 14838, 14840, 14843, 14845, 14850, 14863, 14865, 14867, 14869, 14870, 14871, 14873, 14879, 14880, 14881, 14882, 14883, 14884, 14885, 14886, 14889, 14891, 14892, 14895, 14897, 14901, 14903, 14904, 14905]

Zips in population but not in regulated: 602
[6390, 10018, 10103, 10110, 10111, 10112, 10115, 10119, 10152, 10153, 10154, 10162, 10165, 10167

#### Model Construction Loop, creates:
1. Dec vars for expansion and new construction
2. Adds constraitns and builds expressions for contraints
3. Adds expressions to cost obj function

In [11]:

#iterate through every zip code
for zc in zips_cleaned:                                 #zips_cleaned from demand_classification file
    #expressions for destet removal constraint
    #lhs for total capacity constraint
    lhs_total_cap_expr = 0
    #lhs for 0-5 specific constraint
    lhs_05_cap_expr = 0 

    #grab relevant data
    #demand classificaiton
    #adding try clause because of zip code mismatches, if mismatch, skip zip code
    try:
        #check if in demand_classification
        demand = demand_class[demand_class['zip_code_cleaned'] == zc]['Demand_Classification'].iloc[0]
        #check if in population_calculated
        r05 = populations[populations['zip_code_cleaned'] == zc]['Population_0_5'].iloc[0]
    except:
        continue
    
    #get populations 0-5,5-12
    r05 = populations[populations['zip_code_cleaned'] == zc]['Population_0_5'].iloc[0]
   
    r512 = populations[populations['zip_code_cleaned'] == zc]['Population_0_12'].iloc[0] - r05
    #total kid pop
    r012 = populations[populations['zip_code_cleaned'] == zc]['Population_0_12'].iloc[0]
    
    #existing facilities
    F = regulated[regulated["zip_code_cleaned"] == zc]
    #print(F)
    
    #quick check if this zip code requires new slots, if not, skip zip code
    all_available_slots = F["0-5_capacity"].sum() + F["5-12_capacity"].sum()
    if demand == "High":
        if all_available_slots > (1/2)*r012 and F["0-5_capacity"].sum() > (2/3)*r05:
            #skip this zip code
            continue
    #if normal demand 
    else:
        if all_available_slots > (1/3)*r012 and F["0-5_capacity"].sum() > (2/3)*r05:
            continue

    #facility expansion dec vars and constraints,and add to contraints
    #expansion_vars, list of lists [n05,n512,]
    f_exp_vars = [] 
    for _,f in F.iterrows():
        print(f)
        #current total capacity of facility
        cf = f['total_capacity']
        cf05 = f["0-5_capacity"]
        cf512 = f["5-12_capacity"]
        #skip this facility if total capacity is 0
        if cf == 0:
            continue
        n05 = model.addVar(vtype=GRB.INTEGER, lb=0)
        n512 = model.addVar(vtype=GRB.INTEGER, lb=0)
        model.addConstr(n05 + n512 <= np.min([1.2*cf,500])) #min works because cf is a constant
        #ratio dec var for expansion cost function
        rf = model.addVar(vtype=GRB.CONTINUOUS, lb=0)
        model.addConstr(rf == (n05 + n512) / cf) #note since we filter facilties with 0 cap rf should never = 0 

        #add costs to obj func
        #per slot expansion cost +   extra equipment for new 0-5 slots
        obj += expansion_cost(rf,n05+n512,cf) + 100*n05

        #add values to LHS for desert removal constraints
        lhs_total_cap_expr += n05 + n512 + cf05 + cf512
        lhs_05_cap_expr += n05 + cf05

    #New Locations (types S,M,L)
        
    #dec vars
    #num of new buildings of each type
    b_S = model.addVar(vtype=GRB.INTEGER, lb=0)
    b_M = model.addVar(vtype=GRB.INTEGER, lb=0)
    b_L = model.addVar(vtype=GRB.INTEGER, lb=0)
    #slots generated by new buildings
    #0-5
    n05_S = model.addVar(vtype=GRB.INTEGER, lb=0)
    n05_M = model.addVar(vtype=GRB.INTEGER, lb=0)
    n05_L = model.addVar(vtype=GRB.INTEGER, lb=0)
    #5-12
    n512_S = model.addVar(vtype=GRB.INTEGER, lb=0)
    n512_M = model.addVar(vtype=GRB.INTEGER, lb=0)
    n512_L = model.addVar(vtype=GRB.INTEGER, lb=0)

    #constraints
    #S
    model.addConstr(n05_S + n512_S == 100*b_S)
    model.addConstr(n05_S <= 50*b_S)
    #M
    model.addConstr(n05_M + n512_M == 200*b_M)
    model.addConstr(n05_M <= 100*b_S)
    #L
    model.addConstr(n05_L + n512_L == 400*b_L)
    model.addConstr(n05_L <= 200*b_L)

    #cost function inclusion
    obj += 65000*b_S + 95000*b_M + 115000*b_L + 100*(n05_S + n05_M + n05_L )

    #add values to LHS for desert removal constraints
    lhs_total_cap_expr += n512_S + n512_M + n512_L + n05_S + n05_M + n05_L
    lhs_05_cap_expr += n05_S + n05_M + n05_L

#thats everything right? now we just set the final obj func and destert removal constaraints?
    
    #demand classificaiton based constraints - NOTE WE HAVE TO USE UNSTRICT INEQUALITIES, ???
    if demand == "High":
        model.addConstr(lhs_total_cap_expr >= (1/2)*(r05 + r512))
    elif demand == "Normal":
        model.addConstr(lhs_total_cap_expr >= (1/3)*(r05 + r512))
    else:
        print("Broken demand class!")
        print("Given demand class of : ",demand_class)
        break
    #unconditional 0-5 constraint
    model.addConstr(lhs_05_cap_expr >= (2/3)*r05)


facility_id            837597.000000
infant_capacity             0.000000
toddler_capacity            0.000000
preschool_capacity          0.000000
school_age_capacity        84.000000
children_capacity           0.000000
total_capacity             84.000000
latitude                   40.748836
longitude                 -73.999810
zip_code_cleaned        10001.000000
0-5_capacity                0.000000
5-12_capacity              84.000000
Name: 249, dtype: float64
facility_id            661697.000000
infant_capacity             0.000000
toddler_capacity            0.000000
preschool_capacity          0.000000
school_age_capacity         4.000000
children_capacity          12.000000
total_capacity             16.000000
latitude                   40.748911
longitude                 -74.001546
zip_code_cleaned        10001.000000
0-5_capacity                0.000000
5-12_capacity               4.000000
Name: 3847, dtype: float64
facility_id            837329.000000
infant_capacity       

### Set Objective function to cost expression, optimize

In [12]:
#set the obj function
model.setObjective(obj, GRB.MINIMIZE)


model.optimize()

if model.status == GRB.OPTIMAL:
    print(f"Optimal cost: {model.objVal}")
    for v in model.getVars():
        print(f"{v.varName} = {v.x}")

Gurobi Optimizer version 12.0.3 build v12.0.3rc0 (mac64[arm] - Darwin 23.1.0 23B2073)

CPU model: Apple M3 Pro
Thread count: 11 physical cores, 11 logical processors, using up to 11 threads

Optimize a model with 38450 rows, 53715 columns and 143240 nonzeros
Model fingerprint: 0x6bdf8541
Variable types: 13945 continuous, 39770 integer (0 binary)
Coefficient statistics:
  Matrix range     [1e-03, 4e+02]
  Objective range  [4e-01, 1e+05]
  Bounds range     [0e+00, 0e+00]
  RHS range        [7e-01, 1e+04]
Presolve removed 38164 rows and 53150 columns
Presolve time: 0.93s
Presolved: 286 rows, 565 columns, 1414 nonzeros
Variable types: 0 continuous, 565 integer (0 binary)
Found heuristic solution: objective 5.173338e+08

Root relaxation: objective 5.167805e+08, 5 iterations, 0.00 seconds (0.00 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

*    0     0               0    5.16